In [ ]:
# label transfer with Seurat?

In [2]:
library(Seurat)
library(dplyr)
library(ggplot2)
library(SingleCellExperiment)

In [3]:
# load list of orthologs
om = read.delim('mouse_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'chicken', 'LCA', 'homology_type')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12287     4

mouse  chicken LCA     homology_type   
6 mt-Nd1 ND1     Amniota ortholog_one2one

In [5]:
# load reference
heart.ref = readRDS('~/septation/markers/Qiu/Qiu_E11.5_seuratObj.rds')

In [6]:
# get list of samples
stages = c(rep('stage23', 2), rep(c('stage28', 'stage32'), each = 3))
samples = c('sample3', 'sample10', 'sample5', 'sample10', 'sample11',
           'sample5', 'sample10', 'sample12')

In [7]:
# load data
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(sampleid in 1:length(samples)){
    file0 = paste0(stages[sampleid], '_', samples[sampleid], '_data.rds')
    sce = readRDS(file0)
    
    # subset to mouse 1-1 orthologs
    genelist <- om$mouse[match(rownames(sce), om$chicken)]
    # genelist[1:10]
    
    exp_mat2 = LayerData(sce, assay = 'RNA', layer = 'counts')
    mtd2 = sce@meta.data
    rownames(exp_mat2) = genelist
    exp_mat2 <- exp_mat2[!is.na(rownames(exp_mat2)),]
    
    # dim(exp_mat2)
    heart.query = CreateSeuratObject(counts = exp_mat2, meta.data = mtd2)
    
    # select two technologies for the query datasets
    heart.query <- NormalizeData(heart.query)
    heart.anchors <- FindTransferAnchors(reference = heart.ref, query = heart.query, dims = 1:30,
        reference.reduction = "pca")
    
    # get both levels of anno
    predictions <- TransferData(anchorset = heart.anchors, refdata = heart.ref$major_trajectory, dims = 1:30)
    heart.query <- AddMetaData(heart.query, metadata = predictions)
    
    # add predictions to data.frame to save
    newdf = data.frame(barcode = rownames(heart.query@meta.data), class = heart.query$predicted.id,
                      class_prob = heart.query$prediction.score.max)
    
    predictions <- TransferData(anchorset = heart.anchors, refdata = heart.ref$celltype_update, dims = 1:30)
    heart.query <- AddMetaData(heart.query, metadata = predictions)
    newdf$celltype = heart.query$predicted.id
    newdf$celltype_prob = heart.query$prediction.score.max
    # newdf[1:3,]
    
    # save
    write.table(newdf, file = paste0(stages[sampleid], '_', samples[sampleid], '_Qiu_Seurat_label_transfer.csv'), 
                sep = ',', row.names = F, col.names = T, quote = F)
    
    setTxtProgressBar(pb, sampleid)
}

Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1515 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1143 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1966 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1875 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 1869 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2677 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 2847 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels



Normalizing layer: counts

Projecting cell embeddings

Finding neighborhoods

Finding anchors

	Found 3303 anchors

Finding integration vectors

Finding integration vector weights

Predicting cell labels

Finding integration vectors

Finding integration vector weights

Predicting cell labels

